In [135]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

In [136]:
import time

Initialising the source files containing the English and Dutch Corpus'.

In [137]:
def make_dict_dutch(foreign_l,num_dict_dutch):
    c=1
    for i in foreign_l.keys():
        num_dict_dutch[i]=c
        c+=1
    return num_dict_dutch
        

In [138]:
ENG_FILE_SRC = "/media/ieshaan/Windows/Users/IESHAAN .LAPTOP-U40CT3MF/Downloads/Dataset-20191031T070748Z-001/Dataset/English.txt"
DUTCH_FILE_SRC = "/media/ieshaan/Windows/Users/IESHAAN .LAPTOP-U40CT3MF/Downloads/Dataset-20191031T070748Z-001/Dataset/Dutch.txt"

In [139]:
# Test Files

ENG_TEST_FILE = 'eng.txt'
DUTCH_TEST_FILE = 'dutch.txt'

PROB_FILE -> Contains data of translation probabilities t(e|f).
COUNT_FILE -> Contains data of counts c(e|f)

In [140]:
PROB_FILE = 'condProb.txt'
COUNT_FILE = 'count.txt'

In [141]:
e_file = open(ENG_TEST_FILE,'r',encoding = 'utf-8')
d_file = open(DUTCH_TEST_FILE,'r',encoding = 'utf-8')

In [142]:
dutch = d_file.readlines()
eng = e_file.readlines()

Calculation of total number of sentences in foreign language.

In [143]:
total_no_of_sentences = len(dutch)

The function given below removes all punctuation as well as numbers from the text for ease of translation.

In [144]:
def remove_punc(l):
    for i in range(len(l)):
        l[i] = remove_stuff(l[i])
        l[i] = l[i][:-1]
    return l

In [145]:
def remove_stuff(l):
    a = [ '.' , '\\' , '/' , ',' , ';' , '(' , ')' , '"', "\'",'1','2','3','4','5','6','7','8','9','0','?']
    for i in a:
        l = l.replace(i, "")
    return l

In [146]:
dutch2 = remove_punc(dutch)
eng2 = remove_punc(eng)

In [147]:
from collections import defaultdict

Intialising the dutch and english dictionaries. **Key** -> Words and **Value** -> List of Line Numbers the words occurs in.

In [148]:
dutch_line_no = defaultdict(set)
eng_line_no = defaultdict(set)

Populating the dictionary.

In [149]:
def assign_line_no(doc,dict_lo):
    for i in range(len(doc)):
        t = doc[i].split()
        for m in t:
            dict_lo[m].add(i)
    return dict_lo

In [150]:
dutch_line_no = assign_line_no(dutch2, dutch_line_no)
eng_line_no = assign_line_no(eng2, eng_line_no)

In [151]:
no_of_lines_eng = len(eng_line_no)
no_of_lines_dutch = len(dutch_line_no)

In [152]:
def initialize(foreign_no_of_words,foreign_l,english_l,num_dict_dutch,num_dict_eng):
    probabilities = {} # Initializing proablities
    #count = {} # Count
    counter = 1
    index = -1*(foreign_no_of_words)
    
    num_dict_dutch = make_dict_dutch(foreign_l,num_dict_dutch)

    for i in english_l.keys():
        for j in foreign_l.keys():
            s = i+"_"+j
            probabilities[s] = 1/foreign_no_of_words
            #count[s] = 0
        
        index = write_to_file(probabilities,i,counter,PROB_FILE,foreign_no_of_words,index,num_dict_eng)
        #write_to_file(count,i,counter,COUNT_FILE)
        counter +=1
        probabilities ={}
        
    return True
    

In [153]:
num_dict_eng = {}
num_dict_dutch={}

In [154]:
def write_to_file(probabilities,english_word,counter,file_name,foreign_no_of_words,index,num_dict_eng):
    file = open(file_name,'a')
    #file.write(str(counter)+' '+english_word+'\n')
    num_dict_eng[english_word]=index+foreign_no_of_words
    index=index+foreign_no_of_words
    #print(counter)
    for k,v in probabilities.items():
        file.write('{0} {1}\n'.format(k,v))
    file.close()
    return index

In [155]:
t = time.process_time()
prob = initialize(no_of_lines_dutch,dutch_line_no,eng_line_no,num_dict_dutch,num_dict_eng)
elapsed_time = time.process_time() - t
print(elapsed_time)

1.187351894999999


In [164]:
def finding_probabilities(dutch_sentences, eng_sentences,no_of_sentences,total):
    
    for i in range(no_of_sentences):
        
        du = dutch_sentences[i]
        en = eng_sentences[i]
        
        du_words = du.split()
        en_words = en.split()
        
        # To already retrieve the count
        
        retrieved_count = {}
        retrieved_term_probability = {}
        
        f = open(COUNT_FILE,'r+')
        f2 = open(PROB_FILE,'r+')
        
        lines = f.readlines()
        lines2 = f2.readlines()
        
        #print(len(lines))
        #print(len(lines2))
        
        print(du)
        print(en)
        
        for e in en_words:
            
            for d in du_words:
                
                
                eng_line_no = num_dict_eng[e]
                dutch_line_no = num_dict_dutch[d]
                
                #print("English",e,eng_line_no)
                #print("Dutch",d,dutch_line_no)
                
                line_no = lines[eng_line_no + dutch_line_no-1]
                line_no2 = lines2[eng_line_no + dutch_line_no-1]
                
                #print(line_no," ",line_no2)
                pr = line_no.split()
                pr2 = line_no2.split()
                #print(pr,pr2)
                
                retrieved_count[pr[0]] = float(pr[1])
                retrieved_term_probability[pr2[0]] = float(pr2[1])
                #break
            #break
                
                
        f.close()
        f2.close()
        
        print(retrieved_term_probability)
        print(retrieved_count)
        s_total = {}
        
        for e in en_words:
            
            s_total[e] = 0
            
            for d in du_words:
                
                s = e+'_'+d
                
                #print(s,e)
                
                s_total[e] += retrieved_term_probability[s]
        
        
        for e in en_words:
            
            for d in du_words:
                
                s = e+'_'+d
                
                retrieved_count[s] += retrieved_term_probability[s]/s_total[e]
                
                total[d] += retrieved_term_probability[s]/s_total[e]
                
        # Re-Write into the count_file
        
        f = open(COUNT_FILE,'r+')
        
        m = f.readlines()
        
        for k,v in retrieved_count.items():
            
            t = k.split('_')
            
            eng_line_no=num_dict_eng[t[0]]
            dutch_line_no = num_dict_dutch[t[1]]
            
            final_line_no = eng_line_no + dutch_line_no
            
            m[final_line_no-1] = '{0} {1}\n'.format(k,v)
        
        f.close()
        
        with open(COUNT_FILE,'w') as file:
            file.writelines(m)
            
    
            
        
        
        
        
        
    

In [165]:
#finding_probabilties(dutch,eng,total_no_of_sentences)

In [166]:
def running_function(foreign_l, english_l, dutch_sentences, eng_sentences, no_of_sentences,no_of_iterations = 100):
    
    count = {}
    counter = 1
    for i in english_l.keys():
        for j in foreign_l.keys():
            s = i+"_"+j
            count[s] = 0
            
        write_to_file2(count,i,counter,COUNT_FILE,'w')
        counter += 1
        count = {}
        
    total = {}
    
    for k in foreign_l.keys():
        total[k] = 0
        
    finding_probabilities(dutch_sentences,eng_sentences,no_of_sentences,total)
    
    f = open(COUNT_FILE,'r+')
    f2 = open(PROB_FILE,'r+')
    
    retrieved_count = {}
    retrieved_term_probability = {}
        
    for e in en_words:
            
        for d in du_words:
                
            lines = f.readlines()
            lines2 = f2.readlines()
                
            eng_line_no = num_dict_eng[e]
            dutch_line_no = num_dict_dutch[d]
                
            line_no = lines[eng_line_no + dutch_line_no-1]
            line_no2 = lines2[eng_line_no + dutch_line_no-1]
                
            pr = line_no.split()
            pr2 = line_no2.split()
                
            retrieved_count[pr[0]] = float(pr[1])
            retrieved_term_probability[pr2[0]] = float(pr2[1])
                
                
    f.close()
    f2.close()

    
    
    for d in foreign_l.keys():
        for e in english_l.keys():
            
            s = e+ '_' +d
            retrieved_term_probability[s] = retrieved_count[s]/total[d]  
            
            eng_line_no = num_dict_eng[e]
            dutch_line_no = num_dict_dutch[d]
            
            
            
            
    
    

In [167]:
running_function(dutch_line_no,eng_line_no,dutch2,eng2,len(dutch))

Hervatting van de zitting
Resumption of the session
{'Resumption_Hervatting': 0.0011402508551881414, 'Resumption_van': 0.0011402508551881414, 'Resumption_de': 0.0011402508551881414, 'Resumption_zitting': 0.0011402508551881414, 'of_Hervatting': 0.0011402508551881414, 'of_van': 0.0011402508551881414, 'of_de': 0.0011402508551881414, 'of_zitting': 0.0011402508551881414, 'the_Hervatting': 0.0011402508551881414, 'the_van': 0.0011402508551881414, 'the_de': 0.0011402508551881414, 'the_zitting': 0.0011402508551881414, 'session_Hervatting': 0.0011402508551881414, 'session_van': 0.0011402508551881414, 'session_de': 0.0011402508551881414, 'session_zitting': 0.0011402508551881414}
{'Resumption_Hervatting': 0.0, 'Resumption_van': 0.0, 'Resumption_de': 0.0, 'Resumption_zitting': 0.0, 'of_Hervatting': 0.0, 'of_van': 0.0, 'of_de': 0.0, 'of_zitting': 0.0, 'the_Hervatting': 0.0, 'the_van': 0.0, 'the_de': 0.0, 'the_zitting': 0.0, 'session_Hervatting': 0.0, 'session_van': 0.0, 'session_de': 0.0, 'session_z

Zoals u heeft kunnen constateren is de grote millenniumbug uitgebleven De burgers van een aantal van onze lidstaten zijn daarentegen door verschrikkelijke natuurrampen getroffen
Although as you will have seen the dreaded millennium bug failed to materialise still the people in a number of countries suffered a series of natural disasters that truly were dreadful
{'Although_Zoals': 0.0011402508551881414, 'Although_u': 0.0011402508551881414, 'Although_heeft': 0.0011402508551881414, 'Although_kunnen': 0.0011402508551881414, 'Although_constateren': 0.0011402508551881414, 'Although_is': 0.0011402508551881414, 'Although_de': 0.0011402508551881414, 'Although_grote': 0.0011402508551881414, 'Although_millenniumbug': 0.0011402508551881414, 'Although_uitgebleven': 0.0011402508551881414, 'Although_De': 0.0011402508551881414, 'Although_burgers': 0.0011402508551881414, 'Although_van': 0.0011402508551881414, 'Although_een': 0.0011402508551881414, 'Although_aantal': 0.0011402508551881414, 'Although_onz

U heeft aangegeven dat u deze vergaderperiode een debat wilt over deze rampen
You have requested a debate on this subject in the course of the next few days during this part-session
{'You_U': 0.0011402508551881414, 'You_heeft': 0.0011402508551881414, 'You_aangegeven': 0.0011402508551881414, 'You_dat': 0.0011402508551881414, 'You_u': 0.0011402508551881414, 'You_deze': 0.0011402508551881414, 'You_vergaderperiode': 0.0011402508551881414, 'You_een': 0.0011402508551881414, 'You_debat': 0.0011402508551881414, 'You_wilt': 0.0011402508551881414, 'You_over': 0.0011402508551881414, 'You_rampen': 0.0011402508551881414, 'have_U': 0.0011402508551881414, 'have_heeft': 0.0011402508551881414, 'have_aangegeven': 0.0011402508551881414, 'have_dat': 0.0011402508551881414, 'have_u': 0.0011402508551881414, 'have_deze': 0.0011402508551881414, 'have_vergaderperiode': 0.0011402508551881414, 'have_een': 0.0011402508551881414, 'have_debat': 0.0011402508551881414, 'have_wilt': 0.0011402508551881414, 'have_over': 

Nu wil ik graag op verzoek van een aantal collegas een minuut stilte in acht nemen ter nagedachtenis van de slachtoffers Ik doel hiermee met name op de slachtoffers van het noodweer dat verschillende lidstaten van de Unie heeft geteisterd
In the meantime I should like to observe a minute s silence as a number of Members have requested on behalf of all the victims concerned particularly those of the terrible storms in the various countries of the European Union
{'In_Nu': 0.0011402508551881414, 'In_wil': 0.0011402508551881414, 'In_ik': 0.0011402508551881414, 'In_graag': 0.0011402508551881414, 'In_op': 0.0011402508551881414, 'In_verzoek': 0.0011402508551881414, 'In_van': 0.0011402508551881414, 'In_een': 0.0011402508551881414, 'In_aantal': 0.0011402508551881414, 'In_collegas': 0.0011402508551881414, 'In_minuut': 0.0011402508551881414, 'In_stilte': 0.0011402508551881414, 'In_in': 0.0011402508551881414, 'In_acht': 0.0011402508551881414, 'In_nemen': 0.0011402508551881414, 'In_ter': 0.00114025

Ik wil u vragen deze minuut stilte staande in acht te nemen
Please rise then for this minute s silence
{'Please_Ik': 0.0011402508551881414, 'Please_wil': 0.0011402508551881414, 'Please_u': 0.0011402508551881414, 'Please_vragen': 0.0011402508551881414, 'Please_deze': 0.0011402508551881414, 'Please_minuut': 0.0011402508551881414, 'Please_stilte': 0.0011402508551881414, 'Please_staande': 0.0011402508551881414, 'Please_in': 0.0011402508551881414, 'Please_acht': 0.0011402508551881414, 'Please_te': 0.0011402508551881414, 'Please_nemen': 0.0011402508551881414, 'rise_Ik': 0.0011402508551881414, 'rise_wil': 0.0011402508551881414, 'rise_u': 0.0011402508551881414, 'rise_vragen': 0.0011402508551881414, 'rise_deze': 0.0011402508551881414, 'rise_minuut': 0.0011402508551881414, 'rise_stilte': 0.0011402508551881414, 'rise_staande': 0.0011402508551881414, 'rise_in': 0.0011402508551881414, 'rise_acht': 0.0011402508551881414, 'rise_te': 0.0011402508551881414, 'rise_nemen': 0.0011402508551881414, 'then_Ik

...

Zoals u zich herinnert heb ik opgemerkt waarde collega-voorzitters dat het er niet zozeer toe doet of u voor of tegen de Todin-heffing bent maar dat u van de Commissie en de Raad durft te verlangen dat ze hun mening over dit vraagstuk kenbaar maken
As my fellow chairmen will recall I even mentioned that it was not a matter of knowing whether one was for or against the Tobin tax but of whether one dared to hear what the Commission and the Council thought of it
{'As_Zoals': 0.0011402508551881414, 'As_u': 0.0011402508551881414, 'As_zich': 0.0011402508551881414, 'As_herinnert': 0.0011402508551881414, 'As_heb': 0.0011402508551881414, 'As_ik': 0.0011402508551881414, 'As_opgemerkt': 0.0011402508551881414, 'As_waarde': 0.0011402508551881414, 'As_collega-voorzitters': 0.0011402508551881414, 'As_dat': 0.0011402508551881414, 'As_het': 0.0011402508551881414, 'As_er': 0.0011402508551881414, 'As_niet': 0.0011402508551881414, 'As_zozeer': 0.0011402508551881414, 'As_toe': 0.0011402508551881414, 'As_do

Dat is toch niet teveel gevraagd
It is not a lot to ask
{'It_Dat': 0.0011402508551881414, 'It_is': 0.0011402508551881414, 'It_toch': 0.0011402508551881414, 'It_niet': 0.0011402508551881414, 'It_teveel': 0.0011402508551881414, 'It_gevraagd': 0.0011402508551881414, 'is_Dat': 0.0011402508551881414, 'is_is': 0.0011402508551881414, 'is_toch': 0.0011402508551881414, 'is_niet': 0.0011402508551881414, 'is_teveel': 0.0011402508551881414, 'is_gevraagd': 0.0011402508551881414, 'not_Dat': 0.0011402508551881414, 'not_is': 0.0011402508551881414, 'not_toch': 0.0011402508551881414, 'not_niet': 0.0011402508551881414, 'not_teveel': 0.0011402508551881414, 'not_gevraagd': 0.0011402508551881414, 'a_Dat': 0.0011402508551881414, 'a_is': 0.0011402508551881414, 'a_toch': 0.0011402508551881414, 'a_niet': 0.0011402508551881414, 'a_teveel': 0.0011402508551881414, 'a_gevraagd': 0.0011402508551881414, 'lot_Dat': 0.0011402508551881414, 'lot_is': 0.0011402508551881414, 'lot_toch': 0.0011402508551881414, 'lot_niet': 0

We gaan stemmen over het verzoek van de PPE-DE-Fractie om de mondelinge vragen over hoofdelijke belasting van de agenda te schrappen
We shall proceed to vote on the PPE-DE Group s request that the oral question regarding the capital tax be withdrawn from the agenda
{'We_We': 0.0011402508551881414, 'We_gaan': 0.0011402508551881414, 'We_stemmen': 0.0011402508551881414, 'We_over': 0.0011402508551881414, 'We_het': 0.0011402508551881414, 'We_verzoek': 0.0011402508551881414, 'We_van': 0.0011402508551881414, 'We_de': 0.0011402508551881414, 'We_PPE-DE-Fractie': 0.0011402508551881414, 'We_om': 0.0011402508551881414, 'We_mondelinge': 0.0011402508551881414, 'We_vragen': 0.0011402508551881414, 'We_hoofdelijke': 0.0011402508551881414, 'We_belasting': 0.0011402508551881414, 'We_agenda': 0.0011402508551881414, 'We_te': 0.0011402508551881414, 'We_schrappen': 0.0011402508551881414, 'shall_We': 0.0011402508551881414, 'shall_gaan': 0.0011402508551881414, 'shall_stemmen': 0.0011402508551881414, 'shall_ove

Het Parlement verwerpt het verzoek met  stemmen voor  stemmen tegen en  onthoudingen
Parliament rejected the request with  votes for  votes against and  abstentions
{'Parliament_Het': 0.0011402508551881414, 'Parliament_Parlement': 0.0011402508551881414, 'Parliament_verwerpt': 0.0011402508551881414, 'Parliament_het': 0.0011402508551881414, 'Parliament_verzoek': 0.0011402508551881414, 'Parliament_met': 0.0011402508551881414, 'Parliament_stemmen': 0.0011402508551881414, 'Parliament_voor': 0.0011402508551881414, 'Parliament_tegen': 0.0011402508551881414, 'Parliament_en': 0.0011402508551881414, 'Parliament_onthoudingen': 0.0011402508551881414, 'rejected_Het': 0.0011402508551881414, 'rejected_Parlement': 0.0011402508551881414, 'rejected_verwerpt': 0.0011402508551881414, 'rejected_het': 0.0011402508551881414, 'rejected_verzoek': 0.0011402508551881414, 'rejected_met': 0.0011402508551881414, 'rejected_stemmen': 0.0011402508551881414, 'rejected_voor': 0.0011402508551881414, 'rejected_tegen': 0.0

NameError: name 'en_words' is not defined

In [107]:
def write_to_file2(probabilities,english_word,counter,file_name,mode = 'a'):
    file = open(file_name,'a')
    #file.write(str(counter)+' '+english_word+'\n')
    for k,v in probabilities.items():
        file.write('{0} {1}\n'.format(k,v))
    file.close()

In [75]:
num_dict_eng

{'Resumption': 0,
 'of': 877,
 'the': 1754,
 'session': 2631,
 'I': 3508,
 'declare': 4385,
 'resumed': 5262,
 'European': 6139,
 'Parliament': 7016,
 'adjourned': 7893,
 'on': 8770,
 'Friday': 9647,
 'December': 10524,
 'and': 11401,
 'would': 12278,
 'like': 13155,
 'once': 14032,
 'again': 14909,
 'to': 15786,
 'wish': 16663,
 'you': 17540,
 'a': 18417,
 'happy': 19294,
 'new': 20171,
 'year': 21048,
 'in': 21925,
 'hope': 22802,
 'that': 23679,
 'enjoyed': 24556,
 'pleasant': 25433,
 'festive': 26310,
 'period': 27187,
 'Although': 28064,
 'as': 28941,
 'will': 29818,
 'have': 30695,
 'seen': 31572,
 'dreaded': 32449,
 'millennium': 33326,
 'bug': 34203,
 'failed': 35080,
 'materialise': 35957,
 'still': 36834,
 'people': 37711,
 'number': 38588,
 'countries': 39465,
 'suffered': 40342,
 'series': 41219,
 'natural': 42096,
 'disasters': 42973,
 'truly': 43850,
 'were': 44727,
 'dreadful': 45604,
 'You': 46481,
 'requested': 47358,
 'debate': 48235,
 'this': 49112,
 'subject': 49989

In [76]:
num_dict_dutch

{'Hervatting': 1,
 'van': 2,
 'de': 3,
 'zitting': 4,
 'Ik': 5,
 'verklaar': 6,
 'het': 7,
 'Europees': 8,
 'Parlement': 9,
 'die': 10,
 'op': 11,
 'vrijdag': 12,
 'december': 13,
 'werd': 14,
 'onderbroken': 15,
 'te': 16,
 'zijn': 17,
 'hervat': 18,
 'wens': 19,
 'u': 20,
 'allen': 21,
 'een': 22,
 'gelukkig': 23,
 'nieuwjaar': 24,
 'en': 25,
 'hoop': 26,
 'dat': 27,
 'goede': 28,
 'vakantie': 29,
 'heeft': 30,
 'gehad': 31,
 'Zoals': 32,
 'kunnen': 33,
 'constateren': 34,
 'is': 35,
 'grote': 36,
 'millenniumbug': 37,
 'uitgebleven': 38,
 'De': 39,
 'burgers': 40,
 'aantal': 41,
 'onze': 42,
 'lidstaten': 43,
 'daarentegen': 44,
 'door': 45,
 'verschrikkelijke': 46,
 'natuurrampen': 47,
 'getroffen': 48,
 'U': 49,
 'aangegeven': 50,
 'deze': 51,
 'vergaderperiode': 52,
 'debat': 53,
 'wilt': 54,
 'over': 55,
 'rampen': 56,
 'Nu': 57,
 'wil': 58,
 'ik': 59,
 'graag': 60,
 'verzoek': 61,
 'collegas': 62,
 'minuut': 63,
 'stilte': 64,
 'in': 65,
 'acht': 66,
 'nemen': 67,
 'ter': 68,
 